In [1]:
from tqdm.notebook import tqdm

In [2]:
with open("input_day_05.txt") as f:
    text = f.read()


test = False
if test:
    text = """seeds: 79 14 55 13

seed-to-soil map:
50 98 2
52 50 48

soil-to-fertilizer map:
0 15 37
37 52 2
39 0 15

fertilizer-to-water map:
49 53 8
0 11 42
42 0 7
57 7 4

water-to-light map:
88 18 7
18 25 70

light-to-temperature map:
45 77 23
81 45 19
68 64 13

temperature-to-humidity map:
0 69 1
1 0 69

humidity-to-location map:
60 56 37
56 93 4"""


In [3]:
parts = text.split("\n\n")

seeds = [int(s) for s in parts[0].split(":")[1].split()]
maps = []
for i in range(1, 8):
    maps.append([])
    lines = parts[i].split("\n")
    for l in lines[1:]:
        maps[-1].append([int(n) for n in l.split()])

#import random
#random.Random(0).shuffle(maps)

#maps = maps[:1]


In [4]:
locs = []
for s in seeds:
    curr = s
    for map in maps:
        original_start = curr
        #print(curr)
        #print("analyzing map:", map)
        for r in map:
            #print("analyzing range", r)

            dest_start = r[0]
            source_start = r[1]
            length = r[2]

            if source_start <= original_start < source_start + length:
                #print("using map, ", source_start, curr, source_start + length)
                curr += dest_start - source_start

    locs.append(curr)

print(locs)
print("part 1:", min(locs))


[1970360194, 4284967572, 1349697036, 4270512156, 2662535321, 3661808201, 1747424143, 111627841, 3396941198, 2960374691, 2016800657, 2586973338, 4055854859, 3245172242, 475615938, 3656338298, 3255825948, 1242982568, 3117672709, 3251350486]
part 1: 111627841


In [5]:
seed_ranges = []
for i in range(len(seeds)):
    if i % 2 == 0:
        seed_ranges.append([seeds[i], seeds[i] + seeds[i+1]]) # contains lower but not upper

#seed_ranges = seed_ranges[1:2]
#maps = maps[1:]

out_ranges = []
for seed_range in seed_ranges:
    print("seed range:", seed_range)
    ranges = [seed_range]
    for map in maps:

        unshifted_ranges = ranges.copy()

        print("  map:", map)

        for r in map:

            dest_start = r[0]
            source_start = r[1]
            length = r[2]

            source_end = r[1] + length
            dest_end = r[0] + length

            shift = dest_start - source_start

            print("    line in map:", r)
            print("    source:", source_start, source_end)
            print("    dest:", dest_start, dest_end)

            for unshifted_range in unshifted_ranges.copy():
                print("      unshifted_range:", unshifted_range)
                print("      unshifted_ranges:", unshifted_ranges)
                print("      ranges:", ranges)

                # totally contained case
                if (source_start <= unshifted_range[0] <= source_end) and (source_start <= unshifted_range[1] <= source_end):
                    print("        totally contained")

                    del_index = unshifted_ranges.index(unshifted_range)

                    del unshifted_ranges[del_index]
                    unshifted_ranges.append(unshifted_range)

                    del ranges[del_index]
                    ranges.append([unshifted_range[0] + shift, unshifted_range[1] + shift])

                    print("        new unshifted ranges:", unshifted_ranges[-2:])
                    print("        new ranges:", ranges[-2:])

                # totally outside case
                elif (unshifted_range[1] <= source_start) or (source_end <= unshifted_range[0]):
                    print("        uncontained")

                # partially contained on left
                elif unshifted_range[0] < source_start:
                    print("        contained on left")

                    outside_length = source_start - unshifted_range[0]
                    inside_length = unshifted_range[1] - source_start

                    del_index = unshifted_ranges.index(unshifted_range)

                    del unshifted_ranges[del_index]
                    unshifted_ranges.append([unshifted_range[0], source_start]) # outside range
                    unshifted_ranges.append([source_start, unshifted_range[1]]) # inside range

                    del ranges[del_index]
                    ranges.append([unshifted_range[0], unshifted_range[0] + outside_length]) # outside range
                    ranges.append([source_start + shift, source_start + shift + inside_length]) # inside range

                    print("        new unshifted ranges:", unshifted_ranges[-2:])
                    print("        new ranges:", ranges[-2:])



                # partially contained on right
                elif source_end < unshifted_range[1]:
                    print("        contained on right")

                    outside_length = unshifted_range[1] - source_end
                    inside_length = source_end - unshifted_range[0]

                    del_index = unshifted_ranges.index(unshifted_range)

                    del unshifted_ranges[del_index]
                    unshifted_ranges.append([source_end, unshifted_range[1]]) # outside range
                    unshifted_ranges.append([unshifted_range[0], source_end]) # inside range

                    del ranges[del_index]
                    ranges.append([source_end, source_end + outside_length]) # outside range
                    ranges.append([unshifted_range[0] + shift, unshifted_range[0] + shift + inside_length]) # inside range

                    print("        new unshifted ranges:", unshifted_ranges[-2:])
                    print("        new ranges:", ranges[-2:])



                # otherwise, totally not contained, nothing changes
                else:
                    print("ERROR")

    out_ranges += ranges


print(out_ranges)
print("part 2:", min([r[0] for r in out_ranges]))

# 117250522 is too high
# 62801616 is too low


seed range: [3136945476, 3646674432]
  map: [[2122609492, 2788703865, 117293332], [751770532, 1940296486, 410787026], [2652142963, 2905997197, 464992562], [3442443139, 3721315963, 573651333], [3117135525, 2356966701, 133002244], [742051533, 3370989759, 9718999], [2239902824, 720032349, 393589935], [1162557558, 58715335, 661317014], [1823874572, 2489968945, 298734920], [2633492759, 2351083512, 5883189], [4016094472, 3442443139, 278872824], [58715335, 1256960288, 683336198], [3250137769, 1126389299, 130570989], [2639375948, 1113622284, 12767015]]
    line in map: [2122609492, 2788703865, 117293332]
    source: 2788703865 2905997197
    dest: 2122609492 2239902824
      unshifted_range: [3136945476, 3646674432]
      unshifted_ranges: [[3136945476, 3646674432]]
      ranges: [[3136945476, 3646674432]]
        uncontained
    line in map: [751770532, 1940296486, 410787026]
    source: 1940296486 2351083512
    dest: 751770532 1162557558
      unshifted_range: [3136945476, 3646674432]
     

In [6]:
if test:
    seeds_explicit = []
    for seed_range in seed_ranges:
        for n in range(seed_range[0], seed_range[1]):
            seeds_explicit.append(n)

    print("start:", seeds_explicit)

    seed_records = [[] for _ in range(len(maps[0]))] # seeds for each line in a map

    locs = []
    for s in seeds_explicit:
        curr = s
        #print(maps)
        for map in maps:
            original_start = curr
            #print(curr)
            #print("analyzing map:", map)
            for i_r, r in enumerate(map):
                #print("analyzing range", r)

                dest_start = r[0]
                source_start = r[1]
                length = r[2]

                if source_start <= original_start < source_start + length:
                    #print("using map, ", source_start, curr, source_start + length)
                    curr += dest_start - source_start

                seed_records[i_r].append(curr)

        locs.append(curr)

    for i, sr in enumerate(seed_records):
        print(maps[0][i])
        print("      ", sorted(sr))
    print(sorted(locs))
    # [51,57] [61,67]
    print("slow part 2:", min(locs))
        